In [1]:
import pandas as pd
import numpy as np

pd.options.display.max_columns = None 
pd.options.display.max_rows = None

import timeit

In [44]:
data = pd.read_csv('../Data/train_clean.csv')

In [24]:
def process_data(df):
    df['succesful_play'] = (np.where((df['play_type'] == 'pass')
                                      & (df['yards_gained']>= 6.3), 1,
                                 np.where((df['play_type'] == 'run') 
                                          & (df['yards_gained'] >= 4.4), 1, 0)))
    
    #df['game_setting'] = df['home_team'].str.cat(df['away_team'])
    #dummies = pd.get_dummies(df['posteam'],prefix= 'is_posteam', drop_first = True )
    #df = df.join(dummies)
    
    #dummies_home = pd.get_dummies(df['home_team'],prefix= 'home', drop_first = True )
    #df = df.join(dummies_home)
    
    #dummies_away = pd.get_dummies(df['away_team'],prefix= 'away', drop_first = True )
    #df = df.join(dummies_away)
    
    df['posteam_is_home'] = (np.where(df['posteam_type'] == 'home', 1 , 0))
    
    playtype = pd.get_dummies(df['play_type'], prefix= 'playtype', drop_first = True )
    df = df.join(playtype)
    
    #df['game_half'] = np.where(df['game_half'] == 'Half1', 1, 2)
    
    df['side_of_field_is_hometeam'] = np.where(df['side_of_field'] == df['home_team'], 1, 0)
    
    object_cols = ['posteam', 'posteam_type','defteam',
                   'side_of_field','game_date','time','yrdln', 'desc','play_type']
    df = df.drop(columns = object_cols)
    
    return df 

In [45]:
data_processed = process_data(data)

In [26]:
len(data_processed.game_id.value_counts())

1791

In [56]:
games = data_processed.groupby(['game_id','posteam_is_home', 'home_team', 'away_team'], as_index = False ).sum()

In [47]:
games.head()

game_id  posteam_is_home home_team away_team  play_id  yardline_100  \
0  2009091000                0       PIT       TEN   173096        4622.0   
1  2009091000                1       PIT       TEN   211147        4906.0   
2  2009091300                0       ATL       MIA   157816        3952.0   
3  2009091300                1       ATL       MIA   150335        3369.0   
4  2009091301                0       BAL        KC   160124        3708.0   

   quarter_seconds_remaining  half_seconds_remaining  game_seconds_remaining  \
0                    31739.0                 66839.0                146039.0   
1                    39697.0                 68497.0                151297.0   
2                    27021.0                 61221.0                118821.0   
3                    40950.0                 70650.0                151650.0   
4                    27069.0                 53169.0                116169.0   

   quarter_end  drive  sp  qtr   down  goal_to_go  ydstogo  ydsnet  \
0            3   1130   3  213  148.0         0.0      651    1968   
1            0   1355   4  260  167.0         0.0      676    1982   
2            4    964   2  206  125.0         1.0      545    1701   
3            0    909   5  213  154.0         4.0      650    1875   
4            4    862   5  193  119.0         3.0      487     894   

   yards_gained  shotgun  no_huddle  qb_dropback  qb_kneel  qb_spike  \
0         320.0       18          0         36.0         0         0   
1         357.0       38         14         48.0         0         0   
2         259.0       21          0         33.0         0         0   
3         281.0       17          0         38.0         3         0   
4         188.0       23          2         27.0         0         0   

   qb_scramble  home_timeouts_remaining  away_timeouts_remaining  timeout  \
0            0                      233                      252      3.0   
1            1                      240                      257      5.0   
2            0                      228                      202      0.0   
3            0                      247                      212      5.0   
4            0                      148                      169      4.0   

   posteam_timeouts_remaining  defteam_timeouts_remaining  total_home_score  \
0                       234.0                       218.0               371   
1                       240.0                       257.0               469   
2                       188.0                       208.0               788   
3                       247.0                       212.0               697   
4                       157.0                       138.0              1121   

   total_away_score  posteam_score  defteam_score  score_differential  \
0               345          308.0          344.0               -36.0   
1               495          456.0          495.0               -39.0   
2                27            6.0          717.0              -711.0   
3                70          678.0           70.0               608.0   
4               704          616.0          995.0              -379.0   

   posteam_score_post  defteam_score_post  score_differential_post  \
0               318.0               344.0                    -26.0   
1               469.0               495.0                    -26.0   
2                13.0               717.0                   -704.0   
3               697.0                70.0                    627.0   
4               633.0               995.0                   -362.0   

   no_score_prob  opp_fg_prob  opp_safety_prob  opp_td_prob    fg_prob  \
0      11.943246     8.580310         0.331688    12.523889  19.668746   
1      13.649951     9.042120         0.216976    13.189850  23.725810   
2       8.553595     8.597523         0.226760    12.859169  16.343958   
3       9.146839     6.412542         0.114209     9.695492  24.808687   
4      12.258967     7.644931         0.

In [21]:
""" COLUMNS TO KEEP 
games = games[['game_id', 'posteam_is_home', 'home_team', 'away_team', 'shotgun', 'no_huddle', 'punt_blocked',
                'first_down_rush', 'first_down_pass',
               'first_down_penalty', 'third_down_converted', 'third_down_failed', 'fourth_down_converted',
               'fourth_down_failed', 'interception', 'safety', 'penalty', 'tackled_for_loss', 
              'fumble_lost', 'incomplete_pass', 'qb_hit', 'sack', 'rush_touchdown' , 'pass_touchdown',
               'return_touchdown','field_goal' ,'extra_point', 'two_point_conversion']]

"""

In [57]:
games = games[['game_id', 'posteam_is_home', 'home_team', 'away_team','succesful_play',
               'shotgun', 'no_huddle', 'punt_blocked',
                'first_down_rush', 'first_down_pass',
               'first_down_penalty', 'third_down_converted', 'third_down_failed', 'fourth_down_converted',
               'fourth_down_failed', 'interception', 'safety', 'penalty', 'tackled_for_loss', 
              'fumble_lost', 'incomplete_pass', 'qb_hit', 'sack', 'rush_touchdown' , 'pass_touchdown',
               'return_touchdown','field_goal' ,'extra_point', 'two_point_conversion']]

In [49]:
games

game_id  posteam_is_home home_team away_team  succesful_play  \
0     2009091000                0       PIT       TEN              20   
1     2009091000                1       PIT       TEN              27   
2     2009091300                0       ATL       MIA              21   
3     2009091300                1       ATL       MIA              23   
4     2009091301                0       BAL        KC              12   
5     2009091301                1       BAL        KC              37   
6     2009091302                0       CAR       PHI              20   
7     2009091302                1       CAR       PHI              16   
8     2009091303                0       CIN       DEN              19   
9     2009091303                1       CIN       DEN              25   
10    2009091304                0       CLE       MIN              24   
11    2009091304                1       CLE       MIN              22   
12    2009091305                0       HOU       NYJ              26   
13    2009091305                1       HOU       NYJ              18   
14    2009091306                0       IND       JAC              17   
15    2009091306                1       IND       JAC              20   
16    2009091307                0        NO       DET              14   
17    2009091307                1        NO       DET              35   
18    2009091308                0        TB       DAL              20   
19    2009091308                1        TB       DAL              27   
20    2009091309                0       ARI        SF              14   
21    2009091309                1       ARI        SF              21   
22    2009091310                0       NYG       WAS              18   
23    2009091310                1       NYG       WAS              25   
24    2009091311                0       SEA       STL              18   
25    2009091311                1       SEA       STL              31   
26    2009091312                0        GB       CHI              22   
27    2009091312                1        GB       CHI              21   
28    2009091400                0        NE       BUF              20   
29    2009091400                1        NE       BUF              32   
30    2009091401                0       OAK        SD              25   
31    2009091401                1       OAK        SD              23   
32    2009092000                0       ATL       CAR              25   
33    2009092000                1       ATL       CAR              26   
34    2009092001                0       DET       MIN              20   
35    2009092001                1       DET       MIN              26   
36    2009092002                0        GB       CIN              22   
37    2009092002                1        GB       CIN              22   
38    2009092003                0       JAC       ARI              25   
39    2009092003                1       JAC       ARI              21   
40    2009092004                0        KC       OAK              13   
41    2009092004                1        KC       OAK              35   
42    2009092005                0       NYJ        NE              20   
43    2009092005                1       NYJ        NE              18   
44    2009092006                0       PHI        NO              29   
45    2009092006                1       PHI        NO              28   
46    2009092007                0       TEN       HOU              23   
47    2009092007                1       TEN       HOU              24   
48    2009092008                0       WAS       STL              18   
49    2009092008                1       WAS       STL              27   
50    2009092009                0       BUF        TB              23   
51    2009092009                1       BUF        TB              30   
52    2009092010                0        SF       SEA              18   
53    2009092010                1        SF       SEA              

In [58]:
games_home = games.loc[games['posteam_is_home'] == 1]
games_away = games.loc[games['posteam_is_home'] == 0]

In [60]:
gamedata = games_home.merge(games_away,how = 'inner', on = games_home['game_id'], 
                            suffixes = ('_hometeam', '_awayteam') )

In [61]:
gamedata = gamedata.drop(columns = ['key_0', 'posteam_is_home_hometeam', 'game_id_awayteam',
                                    'posteam_is_home_awayteam','home_team_awayteam', 'away_team_awayteam' ])

In [63]:
gamedata.head()

game_id_hometeam home_team_hometeam away_team_hometeam  \
0        2009091000                PIT                TEN   
1        2009091300                ATL                MIA   
2        2009091301                BAL                 KC   
3        2009091302                CAR                PHI   
4        2009091303                CIN                DEN   

   succesful_play_hometeam  shotgun_hometeam  no_huddle_hometeam  \
0                       27                38                  14   
1                       23                17                   0   
2                       37                20                  43   
3                       16                24                   5   
4                       25                23                   0   

   punt_blocked_hometeam  first_down_rush_hometeam  first_down_pass_hometeam  \
0                    0.0                       1.0                      18.0   
1                    0.0                       3.0                      15.0   
2                    1.0                      11.0                      20.0   
3                    0.0                       4.0                       8.0   
4                    0.0                       4.0                      12.0   

   first_down_penalty_hometeam  third_down_converted_hometeam  \
0                          0.0                            4.0   
1                          1.0                            6.0   
2                          1.0                           10.0   
3                          2.0                            3.0   
4                          0.0                            5.0   

   third_down_failed_hometeam  fourth_down_converted_hometeam  \
0                        10.0                             0.0   
1                         9.0                             0.0   
2                         7.0                             1.0   
3                        13.0                             2.0   
4                        10.0                             1.0   

   fourth_down_failed_hometeam  interception_hometeam  safety_hometeam  \
0                          0.0                    2.0              0.0   
1                          0.0                    0.0              0.0   
2                          0.0                    1.0              0.0   
3                          1.0                    5.0              0.0   
4                          1.0                    2.0              0.0   

   penalty_hometeam  tackled_for_loss_hometeam  fumble_lost_hometeam  \
0               5.0                        3.0                   1.0   
1               4.0                        2.0                   0.0   
2               5.0                        1.0                   0.0   
3               6.0                        4.0                   2.0   
4               4.0                        3.0                   0.0   

   incomplete_pass_hometeam  qb_hit_hometeam  sack_hometeam  \
0                       8.0              7.0            4.0   
1                      14.0              2.0            2.0   
2                      16.0              0.0            1.0   
3                      15.0              9.0            5.0   
4                      10.0              4.0            3.0   

   rush_touchdown_hometeam  pass_touchdown_hometeam  \
0                      0.0                      1.0   
1                      0.0                      2.0   
2                      2.0                      3.0   
3                      1.0                      0.0   
4                      1.0                      0.0   

   return_touchdown_hometeam  field_goal_hometeam  extra_point_hometeam  \
0                        0.0                    2                     1   
1                        0.0                    2                     1   
2                        0.0                    1                     5   
3                        1.0                    1                     1   
4

In [68]:
dummies_home = pd.get_dummies(gamedata['home_team_hometeam'], prefix= 'hometeam', drop_first = True)
dummies_away = pd.get_dummies(gamedata['away_team_hometeam'], prefix= 'awayteam', drop_first = True)


hometeam_ATL  hometeam_BAL  hometeam_BUF  hometeam_CAR  hometeam_CHI  \
0                0             0             0             0             0   
1                1             0             0             0             0   
2                0             1             0             0             0   
3                0             0             0             1             0   
4                0             0             0             0             0   
5                0             0             0             0             0   
6                0             0             0             0             0   
7                0             0             0             0             0   
8                0             0             0             0             0   
9                0             0             0             0             0   
10               0             0             0             0             0   
11               0             0             0             0             0   
12               0             0             0             0             0   
13               0             0             0             0             0   
14               0             0             0             0             0   
15               0             0             0             0             0   
16               1             0             0             0             0   
17               0             0             0             0             0   
18               0             0             0             0             0   
19               0             0             0             0             0   
20               0             0             0             0             0   
21               0             0             0             0             0   
22               0             0             0             0             0   
23               0             0             0             0             0   
24               0             0             0             0             0   
25               0             0             1             0             0   
26               0             0             0             0             0   
27               0             0             0             0             1   
28               0             0             0             0             0   
29               0             0             0             0             0   
30               0             0             0             0             0   
31               0             0             0             0             0   
32               0             1             0             0             0   
33               0             0             0             0             0   
34               0             0             0             0             0   
35               0             0             0             0             0   
36               0             0             0             0             0   
37               0             0             0             0             0   
38               0             0             0             0             0   
39               0             0             0             0             0   
40               0             0             0             0             0   
41               0             0             1             0             0   
42               0             0             0             0             0   
43               0             0             0             0             0   
44               0             0             0             0             0   
45               0             0             0             0             0   
46               0             0             0             0             0   
47               0             0             0             0             0   
48               0             0             0             0             1   
49               0             0             0             0             0   
50               0          

In [72]:
gamedata.shape

(1791, 115)

In [36]:
raw = pd.read_csv('../Data/nfl_train.csv')

/Users/ulrikeanklam/opt/anaconda3/envs/matrix/lib/python3.8/site-packages/IPython/core/interactiveshell.py:3145: DtypeWarning: Columns (42,166,167,168,169,174,175,178,179,182,183,188,189,190,191,194,195,203,204,205,218,219,220,231,232,233,238,240,241,249) have mixed types.Specify dtype option on import or set low_memory=False.
  has_raised = await self.run_ast_nodes(code_ast.body, cell_name,


In [41]:
raw.field_goal_result.value_counts()

made       5759
missed      974
blocked     156
Name: field_goal_result, dtype: int64

In [42]:
raw.extra_point_result.value_counts()

good       7749
failed       75
blocked      43
aborted       7
Name: extra_point_result, dtype: int64

In [43]:
raw.two_point_conv_result.value_counts()

failure    206
success    200
Name: two_point_conv_result, dtype: int64